In [ ]:
# Install required libraries
!pip install openai ipywidgets

import openai
import ipywidgets as widgets
import IPython.display as display
import os
from PIL import Image
import requests
from io import BytesIO

# Set your OpenAI API key as an environment variable
os.environ["OPENAI_API_KEY"] = "Open AI Key"  # Replace with your actual API key

# Initialize the OpenAI client
client = openai.OpenAI()

In [4]:
age_dropdown = widgets.Dropdown(
    options=['7', '8', '9', '10', '11', '12', '13', '14'],
    description='Age:',
    value='7'
)

gender_dropdown = widgets.Dropdown(
    options=['boy', 'girl'],
    description='Gender:',
    value='boy'
)

theme_dropdown = widgets.Dropdown(
    options = ['Friendship & Teamwork', 'Adventure & Exploration', 'Magic & Fantasy', 'Animals & Nature', 'Family & Love'],
    description='Theme:',
    value='Family & Love'
)

moral_dropdown = widgets.Dropdown(
    options =['Honesty', 'Kindness & Helping Others', 'Bravery & Facing Fears','Hard Work & Perseverance','Friendship & Loyalty'],
    description='Moral:',
    value='Honesty'
)

# ✅ Story Output Box
story_output = widgets.Output()

# ✅ Image Output Box
image_output = widgets.Output()

#Function to Generate Story

def generate_story(age, gender, theme, moral):
    prompt = (
    f"You are an expert children's story writer, skilled in crafting engaging, lucid, and imaginative stories "
    f"that quickly capture a child's attention. Your goal is to create a delightful story "
    f"for a {age}-year-old {gender}, using simple and playful language suited for young readers. "

    f"The story should revolve around the theme of '{theme}' and subtly teach the moral lesson of '{moral}'. "
    f"Make it **engaging, creative, and immersive**, ensuring that the child remains entertained while also learning a valuable lesson. "

    f"Keep the story concise, limited to **10-15 sentences**, while ensuring a natural flow with a clear beginning, middle, and happy ending. "
    f"You may reference well-known children's stories for inspiration, adding a fresh twist while keeping it unique and original. "

    f"At the end of the story, provide a list of **3 key scenes** that would make great illustrations in a children's book."
    )

    # Generate text
    chat_completion = client.chat.completions.create(
    messages=[
        {"role": "user", "content": prompt}
    ],
    model="gpt-4o",
    temperature=1,  # Adjust as needed
    top_p=0.8,
    frequency_penalty=0.7,
    presence_penalty=0.8
    )

    story_text = chat_completion.choices[0].message.content.strip()

    # ✅ Extract key illustration scenes
    if "\n\n" in story_text:
        story_parts = story_text.rsplit("\n\n", maxsplit=1)  # Splitting last part
        story = story_parts[0].strip()
        key_scenes = story_parts[1].strip().split("\n")[:3]  # Take first 3 lines as key scenes
    else:
        story, key_scenes = story_text, []

    return story, key_scenes

    #Generating images
def generate_image(description):
    response = client.images.generate(
        model="dall-e-3",  # Use "dall-e-2" if needed
        prompt=f"Children's book illustration of {description}. Cute, colorful, and storybook-style.",
        n=1,  # Number of images
        size="1024x1024"  # Image resolution (other options: "512x512", "256x256")
    )
    return response.data[0].url # Return image URL

# ✅ Function to Handle Button Clicks
def on_button_clicked(b):
    age = age_dropdown.value
    gender = gender_dropdown.value
    theme = theme_dropdown.value
    moral = moral_dropdown.value

    # ✅ Clear previous outputs
    story_output.clear_output()
    image_output.clear_output()

    # ✅ Generate Story
    story, key_scenes = generate_story(age, gender, theme, moral)

    with story_output:
        display.display(display.Markdown(f"### 🌟 Your Story:\n\n{story}"))

    # ✅ Generate and Display Images (without showing key scene text)
    with image_output:
        if key_scenes:
            display.display(display.Markdown("### 🎨 Illustrations:"))
            for scene in key_scenes:
                image_url = generate_image(scene)
                response = requests.get(image_url)
                img = Image.open(BytesIO(response.content))
                display.display(img)

# ✅ Generate Button
generate_button = widgets.Button(description="Generate Story & Images")
generate_button.on_click(on_button_clicked)

# ✅ Display UI Components
display.display(age_dropdown, gender_dropdown, theme_dropdown, moral_dropdown, generate_button, story_output, image_output)

Dropdown(description='Age:', options=('7', '8', '9', '10', '11', '12', '13', '14'), value='7')

Dropdown(description='Gender:', options=('boy', 'girl'), value='boy')

Dropdown(description='Theme:', index=4, options=('Friendship & Teamwork', 'Adventure & Exploration', 'Magic & …

Dropdown(description='Moral:', options=('Honesty', 'Kindness & Helping Others', 'Bravery & Facing Fears', 'Har…

Button(description='Generate Story & Images', style=ButtonStyle())

Output()

Output()